In [1]:
from google.colab import drive
import sys

drive.mount('/content/drive')
%cd /content/drive/MyDrive/hpo_cnn

Mounted at /content/drive
/content/drive/MyDrive/hpo_cnn


# Misc
Run this cell first to unzip the data (ignore if data downloaded)

In [ ]:
import tarfile
import os

archive_path = 'data/ssc.tar.bz2'
extract_to   = 'data/ssc'

#create target dir
os.makedirs(extract_to, exist_ok=True)

with tarfile.open(archive_path, 'r:bz2') as tar:
    tar.extractall(path=extract_to)

In [ ]:
#from hpo_code.utils.io import load_datasets
#train_ds, train_ds2, val_ds = load_datasets(args)

Found 4800 files belonging to 3 classes.
Found 4800 files belonging to 3 classes.
Found 1200 files belonging to 3 classes.


# Hyperparameter Optimization methods

In [ ]:
from types import SimpleNamespace

base_args = SimpleNamespace(
    dir = 'data/ssc/squares-circles',
    imageSize = 32,
    batch1 = 6,
    epochs1 = 5,
    #
    n_convolution1 = 90,
    kernel_size1 = 2,
    strides1 = 1,
    pool1 = 1,
    dropout1 = 0,
    reluLeak1 = 0,
    #
    n_convolution2 = 120,
    kernel_size2 = 5,
    strides2 = 1,
    pool2 = 3,
    dropout2 = 0,
    reluLeak2 = 0.1,
    #
    n_convolution3 = 125,
    kernel_size3 = 2,
    strides3 = 1,
    pool3 = 2,
    dropout3 = 0.1,
    reluLeak3 = 0.1,
    #
    n_dense1 = 60,
    dropoutDense1 = 0.25,
    reluLeakDense1 = 0.12,
    #
    bias_initializer = 0.15,
    kernel_initializer = 'he_normal', # stats distribution to initialize weights
    #
    learning_rate = 1e-4,
    weight_decay = 0.01
)

search_space = {
    "n_dense1":       [20, 40, 60],
    "bias_initializer": [0, 0.20, 0.40, 0.60],
    "reluLeakDense1":  [0, 0.15, 0.30, 0.60],
    "dropoutDense1":   [0, 0.10, 0.20, 0.80]
}

### Random Search

In [ ]:
from hpo_code.hpo_methods import run_random_search
from numpy import random as npr
npr.seed(1)

run_random_search(
    base_args   = base_args,
    search_space= search_space,
    n_trials    = 22,
    results_root= "experiments/random-search"
)

Found 4800 files belonging to 3 classes.
Found 1200 files belonging to 3 classes.


Model: "sequential_84"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling_84 (Rescaling)        │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_336 (LeakyReLU)     │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_336         │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_252               │ (None, 31, 31, 90)     │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_336 (Dropout)           │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_337 (LeakyReLU)     │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_337         │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_253               │ (None, 9, 9, 120)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_337 (Dropout)           │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_338 (LeakyReLU)     │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_338         │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_254               │ (None, 4, 4, 125)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_338 (Dropout)           │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_84 (Flatten)            │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_168 (Dense)               │ (None, 20)             │        40,020 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_339 (LeakyReLU)     │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_339         │ (None, 20)             │            80 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_339 (Dropout)           │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼─────────────

 Total params: 372,198 (1.42 MB)

 Trainable params: 371,488 (1.42 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling_105 (Rescaling)       │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_420 (LeakyReLU)     │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_420         │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_315               │ (None, 31, 31, 90)     │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_420 (Dropout)           │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_421 (LeakyReLU)     │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_421         │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_316               │ (None, 9, 9, 120)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_421 (Dropout)           │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_422 (LeakyReLU)     │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_422         │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_317               │ (None, 4, 4, 125)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_422 (Dropout)           │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_105 (Flatten)           │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_210 (Dense)               │ (None, 40)             │        80,040 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_423 (LeakyReLU)     │ (None, 40)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_423         │ (None, 40)             │           160 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_423 (Dropout)           │ (None, 40)             │             0 │
├─────────────────────────────────┼────────────────────────┼─────────────

 Total params: 412,358 (1.57 MB)

 Trainable params: 411,608 (1.57 MB)

 Non-trainable params: 750 (2.93 KB)

None
model built successfully!
Epoch 1/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 40s 40ms/step - categorical_accuracy: 0.7785 - loss: 0.6157 - val_categorical_accuracy: 0.9733 - val_loss: 0.0987
Epoch 2/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 21s 26ms/step - categorical_accuracy: 0.9138 - loss: 0.2597 - val_categorical_accuracy: 0.9833 - val_loss: 0.0674
Epoch 3/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 43s 29ms/step - categorical_accuracy: 0.9306 - loss: 0.1943 - val_categorical_accuracy: 0.9883 - val_loss: 0.0494
Epoch 4/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 37s 23ms/step - categorical_accuracy: 0.9394 - loss: 0.1843 - val_categorical_accuracy: 0.9950 - val_loss: 0.0237
Epoch 5/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 19s 22ms/step - categorical_accuracy: 0.9563 - loss: 0.1487 - val_categorical_accuracy: 0.9950 - val_loss: 0.0197
19/19 ━━━━━━━━━━━━━━━━━━━━ 8s 274ms/step
trial 22/22 finished
Done! Ran 22 trials in 2934.0 sec. Best trial: #17 with validation accuracy 0.9983


### Hyperband

In [ ]:
from hpo_code.hpo_methods import run_hyperband
from numpy import random as npr
npr.seed(1)

run_hyperband(
    base_args   = base_args,
    search_space= search_space,
    max_iter    = 22,
    eta = 3,
    results_root= "experiments/hyperband"
)

Found 4800 files belonging to 3 classes.
Found 1200 files belonging to 3 classes.


Model: "sequential_62"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling_62 (Rescaling)        │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_248 (LeakyReLU)     │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_248         │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_186               │ (None, 31, 31, 90)     │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_248 (Dropout)           │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_249 (LeakyReLU)     │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_249         │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_187               │ (None, 9, 9, 120)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_249 (Dropout)           │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_250 (LeakyReLU)     │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_250         │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_188               │ (None, 4, 4, 125)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_250 (Dropout)           │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_62 (Flatten)            │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_124 (Dense)               │ (None, 60)             │       120,060 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_251 (LeakyReLU)     │ (None, 60)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_251         │ (None, 60)             │           240 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_251 (Dropout)           │ (None, 60)             │             0 │
├─────────────────────────────────┼────────────────────────┼─────────────

 Total params: 452,518 (1.73 MB)

 Trainable params: 451,728 (1.72 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling_83 (Rescaling)        │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_332 (LeakyReLU)     │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_332         │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_249               │ (None, 31, 31, 90)     │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_332 (Dropout)           │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_333 (LeakyReLU)     │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_333         │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_250               │ (None, 9, 9, 120)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_333 (Dropout)           │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_334 (LeakyReLU)     │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_334         │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_251               │ (None, 4, 4, 125)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_334 (Dropout)           │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_83 (Flatten)            │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_166 (Dense)               │ (None, 20)             │        40,020 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_335 (LeakyReLU)     │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_335         │ (None, 20)             │            80 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_335 (Dropout)           │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼─────────────

 Total params: 372,198 (1.42 MB)

 Trainable params: 371,488 (1.42 MB)

 Non-trainable params: 710 (2.77 KB)

None
model built successfully!
Epoch 1/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 40s 37ms/step - categorical_accuracy: 0.7252 - loss: 0.6635 - val_categorical_accuracy: 0.9633 - val_loss: 0.1485
Epoch 2/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 25s 24ms/step - categorical_accuracy: 0.9088 - loss: 0.2857 - val_categorical_accuracy: 0.9758 - val_loss: 0.0891
Epoch 3/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 23s 28ms/step - categorical_accuracy: 0.9197 - loss: 0.2405 - val_categorical_accuracy: 0.9825 - val_loss: 0.0660
Epoch 4/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 22s 28ms/step - categorical_accuracy: 0.9353 - loss: 0.2239 - val_categorical_accuracy: 0.9925 - val_loss: 0.0435
Epoch 5/5
800/800 ━━━━━━━━━━━━━━━━━━━━ 21s 26ms/step - categorical_accuracy: 0.9496 - loss: 0.1657 - val_categorical_accuracy: 0.9958 - val_loss: 0.0321
19/19 ━━━━━━━━━━━━━━━━━━━━ 5s 208ms/step
Done! Hyperband tested 22 runs in 3816.9s. Best accuracy=0.9967.


### TPE

In [ ]:
from hpo_code.hpo_methods import run_tpe
import numpy as np
from numpy import random as npr
npr.seed(1)

run_tpe(
    base_args   = base_args,
    search_space= search_space,
    n_trials    = 22,
    results_root= "experiments/tpe"
)

Found 4800 files belonging to 3 classes.

Found 1200 files belonging to 3 classes.

  0%|          | 0/22 [00:01<?, ?trial/s, best loss=?]

Model: "sequential_40"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling_40 (Rescaling)        │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_160 (LeakyReLU)     │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_160         │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_120               │ (None, 31, 31, 90)     │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_160 (Dropout)           │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_161 (LeakyReLU)     │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_161         │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_121               │ (None, 9, 9, 120)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_161 (Dropout)           │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_162 (LeakyReLU)     │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_162         │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_122               │ (None, 4, 4, 125)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_162 (Dropout)           │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_40 (Flatten)            │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_80 (Dense)                │ (None, 20)             │        40,020 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_163 (LeakyReLU)     │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_163         │ (None, 20)             │            80 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_163 (Dropout)           │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼─────────────

 Total params: 372,198 (1.42 MB)

 Trainable params: 371,488 (1.42 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling_61 (Rescaling)        │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_244 (LeakyReLU)     │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_244         │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_183               │ (None, 31, 31, 90)     │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_244 (Dropout)           │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_245 (LeakyReLU)     │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_245         │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_184               │ (None, 9, 9, 120)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_245 (Dropout)           │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_246 (LeakyReLU)     │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_246         │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_185               │ (None, 4, 4, 125)      │             0 │
│ (MaxPooling2D)                  │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_246 (Dropout)           │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_61 (Flatten)            │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_122 (Dense)               │ (None, 20)             │        40,020 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_247 (LeakyReLU)     │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_247         │ (None, 20)             │            80 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_247 (Dropout)           │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼─────────────

 Total params: 372,198 (1.42 MB)

 Trainable params: 371,488 (1.42 MB)

 Non-trainable params: 710 (2.77 KB)

None
model built successfully!
Epoch 1/5

  1/800 ━━━━━━━━━━━━━━━━━━━━ 2:03:24 9s/step - categorical_accuracy: 0.3333 - loss: 1.9686
  6/800 ━━━━━━━━━━━━━━━━━━━━ 9s 12ms/step - categorical_accuracy: 0.4139 - loss: 1.5210   
  9/800 ━━━━━━━━━━━━━━━━━━━━ 11s 15ms/step - categorical_accuracy: 0.4488 - loss: 1.4152
 11/800 ━━━━━━━━━━━━━━━━━━━━ 12:27 947ms/step - categorical_accuracy: 0.4654 - loss: 1.3681
 14/800 ━━━━━━━━━━━━━━━━━━━━ 9:36 734ms/step - categorical_accuracy: 0.4792 - loss: 1.3084 
 17/800 ━━━━━━━━━━━━━━━━━━━━ 7:49 600ms/step - categorical_accuracy: 0.4889 - loss: 1.2608
 19/800 ━━━━━━━━━━━━━━━━━━━━ 6:59 537ms/step - categorical_accuracy: 0.4977 - loss: 1.2320
 22/800 ━━━━━━━━━━━━━━━━━━━━ 6:00 463ms/step - categorical_accuracy: 0.5085 - loss: 1.1973
 25/800 ━━━━━━━━━━━━━━━━━━━━ 5:15 408ms/step - categorical_accuracy: 0.5177 - loss: 1.1698
 28/800 ━━━━━━━━━━━━━━━━━━━━ 4:41 364ms/step - categorical_accuracy: 0.5262 - loss: 1.1462
 30/800 ━━━━━━━━━━━━━━━━━━━━ 4:22 341ms/step - c

### TPE with automatic stopping

In [ ]:
from hpo_code.hpo_methods import run_tpe_auto
from numpy import random as npr
npr.seed(1)

run_tpe_auto(
    base_args   = base_args,
    search_space = search_space,
    max_trials    = 22,
    results_root= "experiments/tpe-auto",
    k_folds     = 10,
    min_trials  = 3
)

Found 4800 files belonging to 3 classes.
Found 1200 files belonging to 3 classes.


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ rescaling (Rescaling)           │ (None, 32, 32, 1)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv1 (Conv2D)                  │ (None, 31, 31, 90)     │           450 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu (LeakyReLU)         │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 31, 31, 90)     │           360 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d (MaxPooling2D)    │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 31, 31, 90)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2 (Conv2D)                  │ (None, 27, 27, 120)    │       270,120 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_1 (LeakyReLU)       │ (None, 27, 27, 120)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 27, 27, 120)    │           480 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 9, 9, 120)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv3 (Conv2D)                  │ (None, 8, 8, 125)      │        60,125 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_2 (LeakyReLU)       │ (None, 8, 8, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 8, 8, 125)      │           500 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_2 (MaxPooling2D)  │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 4, 4, 125)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 2000)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 20)             │        40,020 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ leaky_re_lu_3 (LeakyReLU)       │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_3           │ (None, 20)             │            80 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_3 (Dropout)             │ (None, 20)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 3)              │            63 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 372,198 (1.42 MB)

 Trainable params: 371,488 (1.42 MB)

...

 Total params: 372,198 (1.42 MB)

 Trainable params: 371,488 (1.42 MB)

 Non-trainable params: 710 (2.77 KB)

None
Early stopping at trial 4: regret=0.00525 < noise=0.00668
Done! Completed 4 trials in 2532.8s. Best mean loss = 0.0374, Best mean accuracy = 0.9908


({'args': {'dir': 'data/ssc/squares-circles',
   'imageSize': 32,
   'batch1': 6,
   'epochs1': 5,
   'n_convolution1': 90,
   'kernel_size1': 2,
   'strides1': 1,
   'pool1': 1,
   'dropout1': 0,
   'reluLeak1': 0,
   'n_convolution2': 120,
   'kernel_size2': 5,
   'strides2': 1,
   'pool2': 3,
   'dropout2': 0,
   'reluLeak2': 0.1,
   'n_convolution3': 125,
   'kernel_size3': 2,
   'strides3': 1,
   'pool3': 2,
   'dropout3': 0.1,
   'reluLeak3': 0.1,
   'n_dense1': 40,
   'dropoutDense1': 0.2,
   'reluLeakDense1': 0.3,
   'bias_initializer': 0.6,
   'kernel_initializer': 'he_normal',
   'learning_rate': 0.0001,
   'weight_decay': 0.01},
  'mean_loss': 0.03738512471318245,
  'var_loss': 0.00021219875250834684,
  'mean_accuracy': 0.9908333241939544},
 <hpo_code.utils.callbacks.IterationMetrics at 0x7c034b5373d0>)